<a href="https://colab.research.google.com/github/ivynasantino/mineracao-de-dados/blob/master/06-modelo_vetorial/reports/modelo_vetorial.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Modelo Vetorial

Nessa atividade a ideia é implementar várias instanciações do modelo vetorial, a partir dos dados coletados do site El país.

In [0]:
# @title Imports
import pandas as pd
import math
import heapq as hp

import re
from collections import Counter,OrderedDict

import nltk
from nltk.corpus import stopwords
from nltk.tokenize import RegexpTokenizer

nltk.download('stopwords')

In [0]:
# @title Dataframe: El país
elpais = pd.read_csv("https://raw.githubusercontent.com/ivynasantino/mineracao-de-dados/master/02-processamento_de_texto/data/results.csv")

1. Reconstruir o índice considerando o conjunto de dados que indicamos. Esses são os dados coletados por Bernardi e os estaremos usando para facilitar a correção da atividade. Se você já estiver usando esses dados não precisa reconstruir o índice. **ok**

2. Refinar o índice invertido de forma a também incluir o IDF (inverse document frequency) de cada termo do dicionário. (10 pts) **ok**
 **idf = log(M+1)/k**

3. Implementar as seguintes versões do modelo vetorial: (10 pts)

  a) Representação binária
  
  b) TF (lembre-se que esse modelo já está implementado)
  
  c) TF-IDF
  
  d) BM25* (não usaremos Okapi já que os documentos não tem grande variação de tamanho)
  
4. Execute os algoritmos separadamente em 3 consultas de sua escolha e retorne os top-5 documentos mais similares à cada consulta. (10 pts)

5. Compare os resultados encontrados e responda. (20 pts)

  a) Quais modelos você acha que trouxe os melhores resultados? Por que? Inspecione os documentos retornados para melhor embasar sua resposta.

  b) Calcule e reporte o overlap par-a-par entre os resultados de cada modelo ([usando o índice de Jaccard](https://en.wikipedia.org/wiki/Jaccard_index))

A princípio iremos criar algumas funções auxiliares para facilitar o trabalho posteriomente.

In [0]:
def num_of_docs():
  return len(elpais['text'])

### Redefinindo índice invertido

Nesse notebook, a ideia da construção do índice invertido, além dos parâmetros de score e frequência dos documentos, iremos acrescentar o idf.

Para calcular o novo parâmetro, seguimos o seguinte cálculo:

> **IDF = log(M+1) / k**

- M: total de documentos na coleção
- k: frequência do documento


---

Dessa maneira, fazemos esse procedimento logo abaixo:

In [0]:
toker = RegexpTokenizer(r'\w+')
stopwords = stopwords.words("portuguese") 

def buildIndex():
  index = {}
  n = 0
  for doc in elpais.text:
    n += 1
    token = [token for token in toker.tokenize(doc.lower()) 
              if token not in stopwords 
              and len(token) > 3
              and not bool(re.search(r'\d', token))]
    count = list(Counter(token).items())
    for t in count:
      key = t[0]
      freq = t[1]
      idf = math.log(num_of_docs() + 1) / freq
      if key in index.keys():
        if n not in index[key][0]:
          index[key].append((n, freq, idf))
      else:
        index[key] = [(n, freq, idf)]
  return index

In [24]:
index = buildIndex()
index

{'juíza': [(1, 2, 2.760730458931123)],
 'federal': [(1, 2, 2.760730458931123),
  (3, 1, 5.521460917862246),
  (6, 1, 5.521460917862246),
  (7, 3, 1.8404869726207487),
  (15, 1, 5.521460917862246),
  (24, 1, 5.521460917862246),
  (34, 1, 5.521460917862246),
  (37, 2, 2.760730458931123),
  (42, 1, 5.521460917862246),
  (50, 1, 5.521460917862246),
  (113, 1, 5.521460917862246),
  (115, 2, 2.760730458931123),
  (126, 1, 5.521460917862246),
  (134, 1, 5.521460917862246),
  (138, 1, 5.521460917862246),
  (139, 2, 2.760730458931123),
  (144, 1, 5.521460917862246),
  (151, 5, 1.1042921835724493),
  (162, 2, 2.760730458931123),
  (165, 1, 5.521460917862246),
  (166, 1, 5.521460917862246),
  (168, 2, 2.760730458931123),
  (171, 2, 2.760730458931123),
  (173, 4, 1.3803652294655615),
  (178, 1, 5.521460917862246),
  (202, 1, 5.521460917862246),
  (203, 2, 2.760730458931123),
  (204, 1, 5.521460917862246),
  (205, 1, 5.521460917862246),
  (206, 2, 2.760730458931123),
  (207, 2, 2.760730458931123),


Agora, nosso objetivo é implementar as versões do modelo vetorial para:

- Representação binária
- TF
- TF-IDF
- BM25

Para o modelo binário, iremos construir um vetor preenchidos com zeros e de acordo com a presença do termo é setado para um.

In [28]:
print(index.items())

dict_items([('juíza', [(1, 2, 2.760730458931123)]), ('federal', [(1, 2, 2.760730458931123), (3, 1, 5.521460917862246), (6, 1, 5.521460917862246), (7, 3, 1.8404869726207487), (15, 1, 5.521460917862246), (24, 1, 5.521460917862246), (34, 1, 5.521460917862246), (37, 2, 2.760730458931123), (42, 1, 5.521460917862246), (50, 1, 5.521460917862246), (113, 1, 5.521460917862246), (115, 2, 2.760730458931123), (126, 1, 5.521460917862246), (134, 1, 5.521460917862246), (138, 1, 5.521460917862246), (139, 2, 2.760730458931123), (144, 1, 5.521460917862246), (151, 5, 1.1042921835724493), (162, 2, 2.760730458931123), (165, 1, 5.521460917862246), (166, 1, 5.521460917862246), (168, 2, 2.760730458931123), (171, 2, 2.760730458931123), (173, 4, 1.3803652294655615), (178, 1, 5.521460917862246), (202, 1, 5.521460917862246), (203, 2, 2.760730458931123), (204, 1, 5.521460917862246), (205, 1, 5.521460917862246), (206, 2, 2.760730458931123), (207, 2, 2.760730458931123), (208, 2, 2.760730458931123), (210, 1, 5.5214609

In [30]:
binary_vector = [0] * num_of_docs()
binary_rep = {}
for term in index.items():
  print(term)
    

('juíza', [(1, 2, 2.760730458931123)])
('federal', [(1, 2, 2.760730458931123), (3, 1, 5.521460917862246), (6, 1, 5.521460917862246), (7, 3, 1.8404869726207487), (15, 1, 5.521460917862246), (24, 1, 5.521460917862246), (34, 1, 5.521460917862246), (37, 2, 2.760730458931123), (42, 1, 5.521460917862246), (50, 1, 5.521460917862246), (113, 1, 5.521460917862246), (115, 2, 2.760730458931123), (126, 1, 5.521460917862246), (134, 1, 5.521460917862246), (138, 1, 5.521460917862246), (139, 2, 2.760730458931123), (144, 1, 5.521460917862246), (151, 5, 1.1042921835724493), (162, 2, 2.760730458931123), (165, 1, 5.521460917862246), (166, 1, 5.521460917862246), (168, 2, 2.760730458931123), (171, 2, 2.760730458931123), (173, 4, 1.3803652294655615), (178, 1, 5.521460917862246), (202, 1, 5.521460917862246), (203, 2, 2.760730458931123), (204, 1, 5.521460917862246), (205, 1, 5.521460917862246), (206, 2, 2.760730458931123), (207, 2, 2.760730458931123), (208, 2, 2.760730458931123), (210, 1, 5.521460917862246), (2